In [1]:
import rasterio
import glob
import os,sys
from skimage.transform import rescale, resize, downscale_local_mean
from matplotlib import pyplot as plt
import numpy as np
from scipy import misc
import fiona
# import geopandas as gpd
from shapely.geometry import shape
import shapely
from rasterio.mask import mask
from pyproj import Proj, transform

%matplotlib inline

In [2]:
# import the helper functions
from test_unet_helpers import *


In [3]:
# specify scene id for DG data
dg_scene_id = '1030010057062200'

# specify image for 2.0 meter analysis
gt_image_2 = '../../rasters/union_impervious_raster_2_0_0.tif' # desktop
# gt_image_2 = '../rasters/union_impervious_raster_2_0_0.tif' # laptop
#gt_image_2 = 'C:/projects/smart_cities/Denver_Sample_Sites/rasters/union_impervious_raster_2_0.tif'

# specify images for 0.5 meter analysis
gt_image_05 = '../../rasters/union_impervious_raster_0_5.tif' # desktop
# gt_image_05 = '../rasters/union_impervious_raster_0_5.tif' # laptop
#gt_image_05 = 'C:/projects/smart_cities/Denver_Sample_Sites/rasters/union_impervious_raster_0_5.tif'

# specify the shapefile
# shpfile = '../Denver_Sample_Sites/union/union_grid_index256.shp'
shpfile = '../../union/union.shp' # desktop
# shpfile = '../union/union.shp' # desktop
rows = []
with fiona.open(shpfile) as shp:
    crs = shp.crs
#     for s in shp:
#         # rows.append(shape(s['geometry']))
#         pass
        
        
    shp_bounds = shp.bounds


In [4]:
!ls ../../

rasters  smart_Cities  union


Sample Points

1) random sample row and column in GBDX image 
* get lon / lat from Affine object
* sample from rasterio object
 - get row / column from Ground Truth image, create window
 - if window is not NaN, then get it and save both

In [5]:
from gbdxtools import Interface, CatalogImage

# connect to gbdx
gbdx = Interface()

# get the dask array for the 8 band MS image
img_2m = CatalogImage(dg_scene_id, band_type='MS', bbox=shp_bounds, acomp=True)
rows, cols = img_2m.shape[1:]

# get the dask array for the Pansharpened, 4 band image
image_05m = CatalogImage(dg_scene_id, bbox=shp_bounds, acomp=True, pansharpen=True)
rowsP, colsP = image_05m.shape[1:]
pan_factorR = np.floor(rowsP/rows)
pan_factorC = np.floor(colsP/cols)

In [6]:
image_05m.shape, img_2m.shape, os.path.exists(gt_image_2)

((8, 9409, 12924), (8, 2352, 3231), True)

In [7]:
# generate the sample points
# we have some funny stuff from ArcGIS converting the polygons to a raster... so... 
# generate the points within the bounds of the shapefile / DG image array

import random

random.seed(101)

num = 10000
side = 64
coords = []
coords_pan = []
im_patches = []
im_patches_pan = []

with rasterio.open(gt_image_2, 'r') as src:
    
    for i in range(num):
        ran_row, ran_col = random.randrange(0,rows), random.randrange(0,cols) 

        try:
            r_start = ran_row - side/2
            r_end = ran_row + side/2
            c_start = ran_col - side/2
            c_end = ran_col + side/2
            #im_data = img_2m[:, r_start:r_end, c_start:c_end]

            pr_start = ran_row*pan_factorR - side/2
            pr_end = ran_row*pan_factorR + side/2
            pc_start = ran_col*pan_factorC - side/2
            pc_end = ran_col*pan_factorC + side/2
            #im_data_pan = image_05m[:, pr_start:pr_end, pc_start:pc_end]

            # append regardless and check later.

            #############################################################################################################
            ### SHOULD CHECK THE INFORMATION THRESHOLDS BELOW, BUT HERE, TO RESELECT ROWS AND COLUMNS UNTIL IT IS MET ###
            #############################################################################################################

            s_pt = calcXYfromRC(img_2m.affine, (ran_row, ran_col))
            pt_flag = checkWindow(src, s_pt)
            while pt_flag:
                ran_row, ran_col = random.randrange(0,rows), random.randrange(0,cols)
                s_pt = calcXYfromRC(img_2m.affine, (ran_row, ran_col))
                pt_flag = checkWindow(src, s_pt)

            coords.append((ran_row, ran_col))
            coords_pan.append(( int(ran_row*pan_factorR), int(ran_col*pan_factorC)))

            # check for nan
    #         if np.isnan(im_data.mean().compute()):
    #             print(i,im_data)
    #         else:
    #             coords.append((ran_row, ran_col))
    #             coords_pan.append(( int(ran_row*pan_factorR), int(ran_col*pan_factorC)))
    #             #im_patches.append(im_data)
    #             #im_patches_pan.append(im_data_pan)
        except Exception as e:
            print(e)
    #         print('{}, out of bounds'.format(i))
    #         print(r_start, r_end, c_start, c_end)

    coords_arr = np.array(coords)  

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

...

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
name 'self' is not defined
n

KeyboardInterrupt: 

In [ ]:
plt.scatter(coords_arr[:,1], coords_arr[:,0])

In [ ]:
lonlat_MS = [calcXYfromRC(img_2m.affine, pair) for pair in coords]
lonlat_PAN = [calcXYfromRC(image_05m.affine, pair) for pair in coords_pan]

In [ ]:
lonlat_MS[0]
        

In [ ]:
# use the lonlats_* lists to sample the ground truth image. return the histogram if the window is on the border,
# which should be evident if the window extends across
with rasterio.open(gt_image_2, 'r') as src:
    #print(src.crs)

    # cull the lon/lat points by checking if they include nodata pixels
    gt_pts_MS = [assignRC(src, samp_pt) for samp_pt in lonlat_MS]

# do the same for the 0.5 meter ground truth raster
with rasterio.open(gt_image_05, 'r') as src:

    # cull the lon/lat points by checking if they include nodata pixels
    gt_pts_PAN = [assignRC(src, samp_pt) for samp_pt in lonlat_MS]

# remove the None entries from the lists
gt_pts_PAN = [p for p in pts_PAN if p is not None]
gt_pts_MS = [p for p in pts_MS if p is not None]


In [ ]:
## view on map
from shapely.ops import transform
from shapely.geometry import shape, Point

geoms = [Point(pair).buffer(0.00001).__geo_interface__ for pair in lonlat_MS]
    
geojson = {"type": "FetureCollection", "features": []}
for idx, geom in enumerate(geoms):
    g = {
        "type": "Feature",
        "geometry": geom,
        "properties": {"id": idx+1}
    }
    geojson['features'].append(g)
    

print(geojson['features'][0].keys())
# gbdx.vectors.map(features=geojson['features'], zoom=11)
style= {
                        "line-color": '#ff0000',
                        "line-opacity": .99,
                        "line-width": 4
                    }

mapbox_api_key = 'pk.eyJ1Ijoiam9lbWNnY3UiLCJhIjoiY2pla2I1Z2FiMHo2cDJ3bjVwMnJuZWloNiJ9.otjTJOYusw-XYsUohs7ZGg'
gbdx.vectors.map(features=geojson['features'], style=style, zoom=11, api_key=mapbox_api_key)


              

            

## now there are points to generate training samples. Load some classes that will sample the images and return the training arrays.


In [ ]:
# before loading.. save the coordinate objects
with open('gt_pts_MS.pickle', 'wb') as fi:
    pickle.dump(fi, gt_pts_MS)
    
with open('gt_pts_PAN.pickle', 'wb') as fi:
    pickle.dump(fi, gt_pts_PAN)
    
with open('coords.pickle', 'wb') as fi:
    pickle.dump(fi, coords)
    
with open('coords_PAN.pickle', 'wb') as fi:
    pickle.dump(fi, coords_PAN)
    
with open('lonlat_MS.pickle', 'wb') as fi:
    pickle.dump(fi, lonlat_MS)
    
with open('lonlat_PAN.pickle', 'wb') as fi:
    pickle.dump(fi, lonlat_PAN)

In [ ]:
gt_2m_rowcol = [x[1:] for x in gt_pts_MS]
gt_dataset = gtDatasetSampler(gt_image_2, gt_2m_rowcol) # 64 pixel dimension windows
# gt_dataset = gtDatasetSampler(gt_image_2, gt_pts_PAN) # 64 pixel dimension windows
sample = gt_dataset[1]
plt.imshow(sample)
plt.show()

dg_dataset = DigitalGlobeSampler(img_2m, coords)
# dg_dataset = DigitalGlobeSampler(img_pan)
sample = dg_dataset[1]
plt.imshow(sample[0,:,:])
plt.show()

### main chipping code.. first ground truth, then DG

In [ ]:
# non-geospatial images
gt_out_dir_list = ['nogeo_gt_chips_2_0', 'nogeo_gt_chips_0_5']
gt_images = [gt_image_2, gt_image_05]

i=0
window_size = 64
for gt_im, gt_out_dir, samples in zip(gt_images, gt_out_dir_list, [pts_MS, pts_PAN]):
    
    # create the directory if it doesn't exist
    if not os.path.exists(gt_out_dir):
        os.mkdir(gt_out_dir)
    
    # define the basename of the file
    gt_chip_base = 'im_' + gt_out_dir
    
    
    with rasterio.open(gt_im, 'r') as src:
        
        arr = src.read(1)
        # iterate the points
        for i, entry in enumerate(samples[:100]):
            
            r,c = entry[1:]
            
            # check what the sample window would look like
            r_start = int(r - window_size/2)
            r_end = int(r_start + window_size)
            c_start = int(c - window_size/2)
            c_end = int(c_start + window_size)
            win_arr = arr[r_start:r_end, c_start:c_end]
            
            # status
            print('on item {} of {}'.format(i+1, len(samples)))

            # form the output paths
            gt_out_im = '{}_{:0>12}.tif'.format(gt_chip_base, i)
            gt_out_file = os.path.join(gt_out_dir, gt_out_im)

            plt.imsave(gt_out_file, win_arr)
            
            # chip the ground truth image
            #bbox = rioBoundBoxWGS84_toUTM(shp.bounds, {'init': '32613'}, wgs84='4326') # image is in UTM

            #print(gt_im)
            #chip_planet_image(gt_im, bbox, gt_out_file)

            # update counter
            i+=1



In [ ]:
with rasterio.open(r"C:\Projects\smart_cities\impervious_surface_analysis\nogeo_gt_chips_0_5\im_nogeo_gt_chips_0_5_000000000093.tif", 'r') as src:
    arr = src.read(1)
    
plt.hist(arr.ravel())
plt.show()

In [ ]:

gt_out_dir_list = ['gt_chips_2_0', 'gt_chips_0_5']
gt_images = [gt_image_2, gt_image_05]

i=0
for gt_im, gt_out_dir in zip(gt_images, gt_out_dir_list):
    
    # create the directory if it doesn't exist
    if not os.path.exists(gt_out_dir):
        os.mkdir(gt_out_dir)
    
    # define the basename of the file
    gt_chip_base = 'im_' + gt_out_dir
    
    # iterate the geometries
    for i, shp in enumerate(rows):
    
        # status
        print('on item {} of {}'.format(i+1, len(rows)))
        
        # form the output paths
        gt_out_im = '{}_{:0>12}.tif'.format(gt_chip_base, i)
        gt_out_file = os.path.join(gt_out_dir, gt_out_im)

        # chip the ground truth image
        bbox = rioBoundBoxWGS84_toUTM(shp.bounds, {'init': '32613'}, wgs84='4326') # image is in UTM
        
        print(gt_im)
        chip_planet_image(gt_im, bbox, gt_out_file)

        # update counter
        i+=1
        
        



In [ ]:
from gbdxtools import CatalogImage

i=0
skip_ctr=0

# specify processing modes for list
ps_list = [True, False] # pansharpening flag
ac_list = [True, False] # AComp flag

# iterate through the flag possibilities
for ac in ac_list:
    for ps in ps_list:  
    
        if ac and ps: # AComp and Pansharpening

            ## specify directory
            dg_chip_dir = r'dg_chips_AC_PS_0_5'
            
        elif ac and not ps: # AComp and not Pansharpening

            ## specify directory
            dg_chip_dir = r'dg_chips_AC_MS_2_0'
            
        elif not ac and not ps: # not AComp and not Pansharpening

            ## specify directory
            dg_chip_dir = r'dg_chips_noAC_MS_2_0'
            
        else: # not AComp and Pansharpening

            ## specify directory
            dg_chip_dir = r'dg_chips_noAC_PS_0_5'

        
        # make a base for the filenames 
        dg_chip_base = 'im_' + dg_chip_dir
        
        
        ## make the directory if it doesn't exist
        if not os.path.exists(dg_chip_dir):
            os.makedirs(dg_chip_dir)

        ## get the image with AComp and Pansharpen parameters
        img = CatalogImage(dg_scene_id, acomp=ac, pansharpen=ps)           
        
        for i, shp in enumerate(rows):
            
            print ('on item {} of {}, for acomp {} and PS {}'.format(i+1, len(rows), ac, ps))
            # form the output paths
            dg_out_im = '{}_{:0>12}.tif'.format(dg_chip_base, i)
            dg_out_file = os.path.join(dg_chip_dir, dg_out_im)

            # chip the DG image
            chip_dg_image(img, shp.bounds, dg_out_file)
            
            

            # update counter
            i+=1






   

In [ ]:
rows[0]

In [ ]:
image_resized.shape


In [ ]:
dg_arr.max(), image_resized.max(), image.dtype, image_resized.dtype

In [ ]:
import skimage
skimage.__version__

In [ ]:
!conda update skimage